# Choropleth Map: Coronavirus

The objective of this notebook is to create a **choropleth map** with the cases of the coronavirus on March 05, 2020. 

In [36]:
import geopandas as gpd
import json
from bokeh.io import show
from bokeh.models import (CDSView, ColorBar, ColumnDataSource,
                          CustomJS, CustomJSFilter, 
                          GeoJSONDataSource, HoverTool,
                          LinearColorMapper, Slider, LogColorMapper)
from bokeh.layouts import column, row, widgetbox
from bokeh.palettes import brewer
from bokeh.plotting import figure
from bokeh.io import output_notebook
output_notebook()
import pandas as pd
from shapely.geometry import Point, Polygon
import shapely.wkt
import seaborn as sns
from bokeh.models import LinearColorMapper, FixedTicker, ColorBar, NumeralTickFormatter
from bokeh.plotting import figure, output_file, save
from bokeh.io import export_png
from bokeh.plotting import figure, show, output_file
from bokeh.tile_providers import get_provider, Vendors
import numpy as np

Loading BokehJS ...

In [2]:
path = '/Users/cblanesg/Downloads/CHGIS_V4_1990_PROV_PGN-shapefile'

In [3]:
data_shapefiles = gpd.read_file(path)

In [4]:
## Check what CRS has the data 
data_shapefiles.crs
#data_shapefiles = data_shapefiles.to_crs('epsg:4326') ## Change CRS if it's necessary. 

{'init': 'epsg:4326'}

In [5]:
data_shapefiles.head()

GBCODE90    NAME_PY NAME_HZ  SDE2_CHGIS  SDE2_CHG_1    SHAPE_AREA  \
0   340000      Anhui  å®å¾½         0.0         0.0  1.413467e+11   
1   110000    Beijing  åäº¬         0.0         0.0  1.671717e+10   
2   350000     Fujian  ç¦å»º         0.0         0.0  1.230045e+11   
3   620000      Gansu  çè
         0.0         0.0  4.128726e+11   
4   440000  Guangdong  å»£æ±         0.0         0.0  1.774517e+11   

      SHAPE_LEN                                           geometry  
0  2.924949e+06  POLYGON ((117.65244 29.61467, 117.64326 29.609...  
1  7.741163e+05  POLYGON ((116.68565 41.01808, 116.67989 41.009...  
2  4.389994e+06  MULTIPOLYGON (((117.45581 23.78605, 117.44966 ...  
3  7.403188e+06  POLYGON ((105.38684 32.84258, 105.39461 32.834...  
4  5.754889e+06  MULTIPOLYGON (((115.54111 22.78858, 115.53045 ...

In [6]:
## Make a GeoJSON
geosource = GeoJSONDataSource(geojson = data_shapefiles.to_json())

In [7]:
## Download cases of coronavirus
path_info = '/Users/cblanesg/cam.blanes Dropbox/Camila Blanes/deep_dive/GIS/COVID-19/csse_covid_19_data/csse_covid_19_time_series/time_series_19-covid-Confirmed.csv'

In [8]:
info = pd.read_csv(path_info)
info = info[(info['Country/Region'] == 'Mainland China')]
test_info = info[['Province/State', 'Lat', 'Long',
                 '3/5/20']]
test_info.head()

Province/State      Lat      Long  3/5/20
0          Anhui  31.8257  117.2264     990
1        Beijing  40.1824  116.4142     418
2      Chongqing  30.0572  107.8740     576
3         Fujian  26.0789  117.9874     296
4          Gansu  36.0611  103.8343     102

In [50]:
casos = gpd.GeoDataFrame(
test_info, geometry = gpd.points_from_xy(test_info.Long, test_info.Lat))
casos['geometry'].crs = {'init' : 'epsg:4326'}
casos = casos.rename(columns = {'3/5/20': 'casos'})
data_casos = casos[['casos', 'geometry']]
data_casos['size'] = data_casos['casos'] / 10000
data_casos['size2'] = np.log(data_casos['casos']) * 10

/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


In [47]:
geo_shape = gpd.GeoDataFrame(data_casos)
geo_shape.crs = {'init' : 'epsg:4326'}
geo_shape = geo_shape.to_crs(epsg = 3395)
geosource2 = GeoJSONDataSource(geojson = geo_shape.to_json())

/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/pyproj/crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))


## Find the polygon that corresponds to the coordinate point

## 

In [53]:
p1 = figure(title = 'Confirmed Cases of Coronavirus (China: March 05, 2020) ', 
           plot_height = 800, plot_width = 800, 
           toolbar_location = 'below',
           tools = 'pan, wheel_zoom, box_zoom, reset')

p1.xgrid.grid_line_color = None
p1.ygrid.grid_line_color = None
p1.xaxis.major_label_text_color = None
p1.yaxis.major_label_text_color = None
    
tile_provider = get_provider(Vendors.CARTODBPOSITRON_RETINA)# range bounds supplied in web mercator coordinates

p1.add_tile(tile_provider)


color_mapper = LogColorMapper(palette = palette, low = 0, high = 67110)

china = p1.patches('xs', 'ys', source = geosource,
                    fill_color =None,
                      line_color = None,
                      line_width = 0.7,
                      fill_alpha = 1)

p1.circle(x='x', y='y', size= 'size2', source = geosource2, 
         line_color="#FF0000", 
         fill_color="#FF0000",
         fill_alpha=0.05)

p1.add_tools(HoverTool(tooltips = [('Número de Casos','@casos')]))

#output_file("china_coronavirus.html")
#save(p1)
show(p1)